Create a spark session and load the Housing Data set

In [0]:
from pyspark.sql import SparkSession


In [0]:
# File location and type
file_location = "/FileStore/tables/red_or_white_wine-6.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","
 
# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)
 

Data pre-processing

In [0]:
# Import the required libraries
 
from pyspark.sql.functions import datediff,date_format,to_date,to_timestamp

In [0]:
import pyspark.sql.functions as f

In [0]:
df=df.withColumn('type',df.type.cast('integer'))

In [0]:
data = df.select(['fixed acidity',
'volatile acidity',
'citric acid',
'residual sugar',
'chlorides',
'free sulfur dioxide',
'total sulfur dioxide',
'density',
'pH',
'sulphates',
'alcohol',
'quality',
'type'
])

In [0]:
df.printSchema()

root
 |-- fixed acidity: double (nullable = true)
 |-- volatile acidity: double (nullable = true)
 |-- citric acid: double (nullable = true)
 |-- residual sugar: double (nullable = true)
 |-- chlorides: double (nullable = true)
 |-- free sulfur dioxide: double (nullable = true)
 |-- total sulfur dioxide: double (nullable = true)
 |-- density: double (nullable = true)
 |-- pH: double (nullable = true)
 |-- sulphates: double (nullable = true)
 |-- alcohol: double (nullable = true)
 |-- quality: integer (nullable = true)
 |-- type: integer (nullable = true)



In [0]:
df=df.dropna()

In [0]:
print((df.count(),len(df.columns)))

(0, 13)


In [0]:
# Create a 70-30 train test split
 
train_data,test_data=data.randomSplit([0.7,0.3])

In [0]:
print((train_data.count(),len(train_data.columns)))

(4567, 13)


In [0]:
print((test_data.count(),len(test_data.columns)))

(1930, 13)


In [0]:
# Import the required libraries
 
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.feature import VectorAssembler,StringIndexer ,OneHotEncoder
from pyspark.ml import Pipeline
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

Building the Baseline Linear Regression model

In [0]:
type_indexer = StringIndexer(inputCol='type',outputCol='type_index',handleInvalid='keep')

In [0]:
assembler= VectorAssembler(
                inputCols=['fixed acidity',
'volatile acidity',
'citric acid',
'residual sugar',
'chlorides',
'free sulfur dioxide',
'total sulfur dioxide',
'density',
'pH',
'sulphates',
'alcohol',
'type_index'
],
outputCol="features")

In [0]:
pipe = Pipeline(stages= [type_indexer,assembler])


In [0]:
fitted_pipe=pipe.fit(train_data)

In [0]:
train_data=fitted_pipe.transform(train_data)
display(train_data)

fixed acidity volatile acidity citric acid residual sugar chlorides free sulfur dioxide total sulfur dioxide density pH sulphates alcohol quality type type_index features 3.8 0.31 0.02 11.1 0.036 20.0 114.0 0.99248 3.75 0.44 12.4 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(3.8, 0.31, 0.02, 11.1, 0.036, 20.0, 114.0, 0.99248, 3.75, 0.44, 12.4, 0.0)) 3.9 0.225 0.4 4.2 0.03 29.0 118.0 0.989 3.57 0.36 12.8 8 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(3.9, 0.225, 0.4, 4.2, 0.03, 29.0, 118.0, 0.989, 3.57, 0.36, 12.8, 0.0)) 4.2 0.215 0.23 5.1 0.041 64.0 157.0 0.99688 3.42 0.44 8.0 3 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.2, 0.215, 0.23, 5.1, 0.041, 64.0, 157.0, 0.99688, 3.42, 0.44, 8.0, 0.0)) 4.4 0.32 0.39 4.3 0.03 31.0 127.0 0.98904 3.46 0.36 12.8 8 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.4, 0.32, 0.39, 4.3, 0.03, 31.0, 127.0, 0.98904, 3.46, 0.36, 12.8, 0.0)) 4.4 0.46 0.1 2.8 0.024 31.0 111.0 0.98816 3.48 0.34 13.1 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.4, 0.46, 0.1, 2.8, 0.024, 31.0, 111.0, 0.98816, 3.48, 0.34, 13.1, 0.0)) 4.4 0.54 0.09 5.1 0.038 52.0 97.0 0.99022 3.41 0.4 12.2 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.4, 0.54, 0.09, 5.1, 0.038, 52.0, 97.0, 0.99022, 3.41, 0.4, 12.2, 0.0)) 4.5 0.19 0.21 0.95 0.033 89.0 159.0 0.99332 3.34 0.42 8.0 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.5, 0.19, 0.21, 0.95, 0.033, 89.0, 159.0, 0.99332, 3.34, 0.42, 8.0, 0.0)) 4.6 0.445 0.0 1.4 0.053 11.0 178.0 0.99426 3.79 0.55 10.2 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.6, 0.445, 0.0, 1.4, 0.053, 11.0, 178.0, 0.99426, 3.79, 0.55, 10.2, 0.0)) 4.6 0.52 0.15 2.1 0.054 8.0 65.0 0.9934 3.9 0.56 13.1 4 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.6, 0.52, 0.15, 2.1, 0.054, 8.0, 65.0, 0.9934, 3.9, 0.56, 13.1, 0.0)) 4.7 0.145 0.29 1.0 0.042 35.0 90.0 0.9908 3.76 0.49 11.3 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.145, 0.29, 1.0, 0.042, 35.0, 90.0, 0.9908, 3.76, 0.49, 11.3, 0.0)) 4.7 0.335 0.14 1.3 0.036 69.0 168.0 0.99212 3.47 0.46 10.5 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.335, 0.14, 1.3, 0.036, 69.0, 168.0, 0.99212, 3.47, 0.46, 10.5, 0.0)) 4.7 0.455 0.18 1.9 0.036 33.0 106.0 0.98746 3.21 0.83 14.0 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.455, 0.18, 1.9, 0.036, 33.0, 106.0, 0.98746, 3.21, 0.83, 14.0, 0.0)) 4.7 0.6 0.17 2.3 0.058 17.0 106.0 0.9932 3.85 0.6 12.9 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.6, 0.17, 2.3, 0.058, 17.0, 106.0, 0.9932, 3.85, 0.6, 12.9, 0.0)) 4.7 0.67 0.09 1.0 0.02 5.0 9.0 0.98722 3.3 0.34 13.6 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.67, 0.09, 1.0, 0.02, 5.0, 9.0, 0.98722, 3.3, 0.34, 13.6, 0.0)) 4.7 0.785 0.0 3.4 0.036 23.0 134.0 0.98981 3.53 0.92 13.8 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.7, 0.785, 0.0, 3.4, 0.036, 23.0, 134.0, 0.98981, 3.53, 0.92, 13.8, 0.0)) 4.8 0.13 0.32 1.2 0.042 40.0 98.0 0.9898 3.42 0.64 11.8 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.8, 0.13, 0.32, 1.2, 0.042, 40.0, 98.0, 0.9898, 3.42, 0.64, 11.8, 0.0)) 4.8 0.17 0.28 2.9 0.03 22.0 111.0 0.9902 3.38 0.34 11.3 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.8, 0.17, 0.28, 2.9, 0.03, 22.0, 111.0, 0.9902, 3.38, 0.34, 11.3, 0.0)) 4.8 0.21 0.21 10.2 0.037 17.0 112.0 0.99324 3.66 0.48 12.2 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.8, 0.21, 0.21, 10.2, 0.037, 17.0, 112.0, 0.99324, 3.66, 0.48, 12.2, 0.0)) 4.8 0.225 0.38 1.2 0.074 47.0 130.0 0.99132 3.31 0.4 10.3 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.8, 0.225, 0.38, 1.2, 0.074, 47.0, 130.0, 0.99132, 3.31, 0.4, 10.3, 0.0)) 4.8 0.26 0.23 10.6 0.034 23.0 111.0 0.99274 3.46 0.28 11.5 7 null 0.0 Map(vectorType -> dense, length -> 12

In [0]:
#Create an object for the Linear Regression model
 
lr_model = LinearRegression(labelCol='quality')

In [0]:
# Fit the model on the train data
 
fit_model = lr_model.fit(train_data.select(['features','quality']))

In [0]:
# Transform the test data using the model to predict the duration
 
test_data=fitted_pipe.transform(test_data)
display(test_data)

fixed acidity volatile acidity citric acid residual sugar chlorides free sulfur dioxide total sulfur dioxide density pH sulphates alcohol quality type type_index features 4.2 0.17 0.36 1.8 0.029 93.0 161.0 0.98999 3.65 0.89 12.0 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.2, 0.17, 0.36, 1.8, 0.029, 93.0, 161.0, 0.98999, 3.65, 0.89, 12.0, 0.0)) 4.9 0.335 0.14 1.3 0.036 69.0 168.0 0.99212 3.47 0.46 10.46666667 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.335, 0.14, 1.3, 0.036, 69.0, 168.0, 0.99212, 3.47, 0.46, 10.46666667, 0.0)) 4.9 0.345 0.34 1.0 0.068 32.0 143.0 0.99138 3.24 0.4 10.1 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.345, 0.34, 1.0, 0.068, 32.0, 143.0, 0.99138, 3.24, 0.4, 10.1, 0.0)) 4.9 0.345 0.34 1.0 0.068 32.0 143.0 0.99138 3.24 0.4 10.1 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.345, 0.34, 1.0, 0.068, 32.0, 143.0, 0.99138, 3.24, 0.4, 10.1, 0.0)) 5.0 0.235 0.27 11.75 0.03 34.0 118.0 0.9954 3.07 0.5 9.4 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.235, 0.27, 11.75, 0.03, 34.0, 118.0, 0.9954, 3.07, 0.5, 9.4, 0.0)) 5.0 0.255 0.22 2.7 0.043 46.0 153.0 0.99238 3.75 0.76 11.3 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.255, 0.22, 2.7, 0.043, 46.0, 153.0, 0.99238, 3.75, 0.76, 11.3, 0.0)) 5.0 0.27 0.32 4.5 0.032 58.0 178.0 0.98956 3.45 0.31 12.6 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.27, 0.32, 4.5, 0.032, 58.0, 178.0, 0.98956, 3.45, 0.31, 12.6, 0.0)) 5.0 0.33 0.16 1.5 0.049 10.0 97.0 0.9917 3.48 0.44 10.7 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.16, 1.5, 0.049, 10.0, 97.0, 0.9917, 3.48, 0.44, 10.7, 0.0)) 5.0 0.33 0.16 1.5 0.049 10.0 97.0 0.9917 3.48 0.44 10.7 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.16, 1.5, 0.049, 10.0, 97.0, 0.9917, 3.48, 0.44, 10.7, 0.0)) 5.0 0.33 0.18 4.6 0.032 40.0 124.0 0.99114 3.18 0.4 11.0 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.18, 4.6, 0.032, 40.0, 124.0, 0.99114, 3.18, 0.4, 11.0, 0.0)) 5.0 0.44 0.04 18.6 0.039 38.0 128.0 0.9985 3.37 0.57 10.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.44, 0.04, 18.6, 0.039, 38.0, 128.0, 0.9985, 3.37, 0.57, 10.2, 0.0)) 5.0 1.02 0.04 1.4 0.045 41.0 85.0 0.9938 3.75 0.48 10.5 4 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 1.02, 0.04, 1.4, 0.045, 41.0, 85.0, 0.9938, 3.75, 0.48, 10.5, 0.0)) 5.1 0.14 0.25 0.7 0.039 15.0 89.0 0.9919 3.22 0.43 9.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.14, 0.25, 0.7, 0.039, 15.0, 89.0, 0.9919, 3.22, 0.43, 9.2, 0.0)) 5.1 0.21 0.28 1.4 0.047 48.0 148.0 0.99168 3.5 0.49 10.4 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.21, 0.28, 1.4, 0.047, 48.0, 148.0, 0.99168, 3.5, 0.49, 10.4, 0.0)) 5.1 0.26 0.34 6.4 0.034 26.0 99.0 0.99449 3.23 0.41 9.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.26, 0.34, 6.4, 0.034, 26.0, 99.0, 0.99449, 3.23, 0.41, 9.2, 0.0)) 5.1 0.3 0.3 2.3 0.048 40.0 150.0 0.98944 3.29 0.46 12.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.3, 0.3, 2.3, 0.048, 40.0, 150.0, 0.98944, 3.29, 0.46, 12.2, 0.0)) 5.1 0.33 0.22 1.6 0.027 18.0 89.0 0.9893 3.51 0.38 12.5 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.33, 0.22, 1.6, 0.027, 18.0, 89.0, 0.9893, 3.51, 0.38, 12.5, 0.0)) 5.1 0.33 0.27 6.7 0.022 44.0 129.0 0.99221 3.36 0.39 11.0 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.33, 0.27, 6.7, 0.022, 44.0, 129.0, 0.99221, 3.36, 0.39, 11.0, 0.0)) 5.1 0.52 0.06 2.7 0.052 30.0 79.0 0.9932 3.32 0.43 9.3 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.52, 0.06, 2.7, 0.052, 30.0, 79.0, 0.9932, 3.32, 0.43, 9.3, 0.0)) 5.2 0.2 0.27 3.2 0.047 16.0 93.0 0.99235 3.44 0.53 10.1 7 null 0.0 Map(vectorType -> dense,

In [0]:
# Store the results in a dataframe
 
results = fit_model.transform(test_data)
display(results)

fixed acidity volatile acidity citric acid residual sugar chlorides free sulfur dioxide total sulfur dioxide density pH sulphates alcohol quality type type_index features prediction 4.2 0.17 0.36 1.8 0.029 93.0 161.0 0.98999 3.65 0.89 12.0 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.2, 0.17, 0.36, 1.8, 0.029, 93.0, 161.0, 0.98999, 3.65, 0.89, 12.0, 0.0)) 6.953839175666449 4.9 0.335 0.14 1.3 0.036 69.0 168.0 0.99212 3.47 0.46 10.46666667 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.335, 0.14, 1.3, 0.036, 69.0, 168.0, 0.99212, 3.47, 0.46, 10.46666667, 0.0)) 5.769099402927608 4.9 0.345 0.34 1.0 0.068 32.0 143.0 0.99138 3.24 0.4 10.1 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.345, 0.34, 1.0, 0.068, 32.0, 143.0, 0.99138, 3.24, 0.4, 10.1, 0.0)) 5.389829584107311 4.9 0.345 0.34 1.0 0.068 32.0 143.0 0.99138 3.24 0.4 10.1 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(4.9, 0.345, 0.34, 1.0, 0.068, 32.0, 143.0, 0.99138, 3.24, 0.4, 10.1, 0.0)) 5.389829584107311 5.0 0.235 0.27 11.75 0.03 34.0 118.0 0.9954 3.07 0.5 9.4 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.235, 0.27, 11.75, 0.03, 34.0, 118.0, 0.9954, 3.07, 0.5, 9.4, 0.0)) 5.725944300856398 5.0 0.255 0.22 2.7 0.043 46.0 153.0 0.99238 3.75 0.76 11.3 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.255, 0.22, 2.7, 0.043, 46.0, 153.0, 0.99238, 3.75, 0.76, 11.3, 0.0)) 6.367182079275853 5.0 0.27 0.32 4.5 0.032 58.0 178.0 0.98956 3.45 0.31 12.6 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.27, 0.32, 4.5, 0.032, 58.0, 178.0, 0.98956, 3.45, 0.31, 12.6, 0.0)) 6.451913432616969 5.0 0.33 0.16 1.5 0.049 10.0 97.0 0.9917 3.48 0.44 10.7 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.16, 1.5, 0.049, 10.0, 97.0, 0.9917, 3.48, 0.44, 10.7, 0.0)) 5.7161997211470315 5.0 0.33 0.16 1.5 0.049 10.0 97.0 0.9917 3.48 0.44 10.7 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.16, 1.5, 0.049, 10.0, 97.0, 0.9917, 3.48, 0.44, 10.7, 0.0)) 5.7161997211470315 5.0 0.33 0.18 4.6 0.032 40.0 124.0 0.99114 3.18 0.4 11.0 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.33, 0.18, 4.6, 0.032, 40.0, 124.0, 0.99114, 3.18, 0.4, 11.0, 0.0)) 5.905640778174988 5.0 0.44 0.04 18.6 0.039 38.0 128.0 0.9985 3.37 0.57 10.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 0.44, 0.04, 18.6, 0.039, 38.0, 128.0, 0.9985, 3.37, 0.57, 10.2, 0.0)) 5.963390247855003 5.0 1.02 0.04 1.4 0.045 41.0 85.0 0.9938 3.75 0.48 10.5 4 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.0, 1.02, 0.04, 1.4, 0.045, 41.0, 85.0, 0.9938, 3.75, 0.48, 10.5, 0.0)) 4.915462529156937 5.1 0.14 0.25 0.7 0.039 15.0 89.0 0.9919 3.22 0.43 9.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.14, 0.25, 0.7, 0.039, 15.0, 89.0, 0.9919, 3.22, 0.43, 9.2, 0.0)) 5.485594233223985 5.1 0.21 0.28 1.4 0.047 48.0 148.0 0.99168 3.5 0.49 10.4 5 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.21, 0.28, 1.4, 0.047, 48.0, 148.0, 0.99168, 3.5, 0.49, 10.4, 0.0)) 5.900999652631263 5.1 0.26 0.34 6.4 0.034 26.0 99.0 0.99449 3.23 0.41 9.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.26, 0.34, 6.4, 0.034, 26.0, 99.0, 0.99449, 3.23, 0.41, 9.2, 0.0)) 5.450708053616609 5.1 0.3 0.3 2.3 0.048 40.0 150.0 0.98944 3.29 0.46 12.2 6 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.3, 0.3, 2.3, 0.048, 40.0, 150.0, 0.98944, 3.29, 0.46, 12.2, 0.0)) 6.256460346058322 5.1 0.33 0.22 1.6 0.027 18.0 89.0 0.9893 3.51 0.38 12.5 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.33, 0.22, 1.6, 0.027, 18.0, 89.0, 0.9893, 3.51, 0.38, 12.5, 0.0)) 6.331973295775551 5.1 0.33 0.27 6.7 0.022 44.0 129.0 0.99221 3.36 0.39 11.0 7 null 0.0 Map(vectorType -> dense, length -> 12, values -> List(5.1, 0.33, 0.27, 6.7, 0.022, 44.0, 129.

In [0]:
results.select(['quality','prediction']).show()

+-------+------------------+
|quality|        prediction|
+-------+------------------+
|      7| 6.953839175666449|
|      5| 5.769099402927608|
|      5| 5.389829584107311|
|      5| 5.389829584107311|
|      6| 5.725944300856398|
|      6| 6.367182079275853|
|      7| 6.451913432616969|
|      6|5.7161997211470315|
|      6|5.7161997211470315|
|      6| 5.905640778174988|
|      6| 5.963390247855003|
|      4| 4.915462529156937|
|      6| 5.485594233223985|
|      5| 5.900999652631263|
|      6| 5.450708053616609|
|      6| 6.256460346058322|
|      7| 6.331973295775551|
|      7| 5.999348827001015|
|      5| 5.143082964836811|
|      7| 5.856126333496544|
+-------+------------------+
only showing top 20 rows



Evaluating the model

In [0]:
test_results = fit_model.evaluate(test_data)

In [0]:
test_results.residuals.show()

+--------------------+
|           residuals|
+--------------------+
|0.046160824333551176|
| -0.7690994029276084|
| -0.3898295841073107|
| -0.3898295841073107|
|  0.2740556991436023|
| -0.3671820792758531|
|  0.5480865673830309|
| 0.28380027885296855|
| 0.28380027885296855|
| 0.09435922182501244|
| 0.03660975214499729|
| -0.9154625291569367|
|  0.5144057667760151|
| -0.9009996526312634|
|  0.5492919463833914|
|-0.25646034605832213|
|  0.6680267042244488|
|  1.0006511729989853|
|-0.14308296483681104|
|  1.1438736665034561|
+--------------------+
only showing top 20 rows



In [0]:
test_results.rootMeanSquaredError

Out[26]: 0.7255952613565323